In [1]:
%cd C:/Users/alapa/funiegan/funiegan_1.0

C:\Users\alapa\funiegan\funiegan_1.0


C:\Users\alapa\AppData\Local\Packages\PythonSoftwareFoundation.Python.3.12_qbz5n2kfra8p0\LocalCache\local-packages\Python312\site-packages\IPython\core\magics\osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


In [2]:
import os
import time
import numpy as np
from PIL import Image
from glob import glob
from ntpath import basename
from os.path import join, exists
# pytorch libs
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.autograd import Variable
from torchvision.utils import save_image
import torchvision.transforms as transforms

In [3]:
### loop checking all models

import argparse

for i in range(1,21):

    generator = (f"checkpoints/FunieGAN(NLSCA_AdaB_L_RA)/EUVP/generator_{i}.pth")
    print(generator) 
    parser = argparse.ArgumentParser()
    parser.add_argument("--data_dir", type=str, default=r"EUVP/test_samples/Inp")
    parser.add_argument("--sample_dir", type=str, default=r"EUVP/test_samples/result/NLSCA_AdaB_L_RA")
    parser.add_argument("--model_name", type=str, default="funiegan") # or "ugan"
    parser.add_argument("--model_path", type=str, default=generator)
    opt,unknown = parser.parse_known_args()

    print(opt.model_path)

    assert exists(opt.model_path), "model not found"
    os.makedirs(opt.sample_dir, exist_ok=True)
    is_cuda = torch.cuda.is_available()
    Tensor = torch.cuda.FloatTensor if is_cuda else torch.FloatTensor 

    if opt.model_name.lower()=='funiegan':
        from PyTorch.nets import SCAfuinegan
        model = SCAfuinegan.GeneratorFunieGAN()
    elif opt.model_name.lower()=='ugan':
        from nets.ugan import UGAN_Nets
        model = UGAN_Nets(base_model='pix2pix').netG
    else: 
        # other models
        pass

    model.load_state_dict(torch.load(opt.model_path, weights_only=True))
    if is_cuda: model.cuda()
    model.eval()
    print ("Loaded model from %s" % (opt.model_path))

    ## data pipeline
    img_width, img_height, channels = 256, 256, 3
    transforms_ = [transforms.Resize((img_height, img_width), Image.BICUBIC),
                transforms.ToTensor(),
                transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),]
    transform = transforms.Compose(transforms_)

    dir_name = join(opt.sample_dir, f"generator_{i}")
    os.makedirs(dir_name, exist_ok=True)

    times = []
    test_files = sorted(glob(join(opt.data_dir, "*.*")))
    for path in test_files:
        inp_img = transform(Image.open(path))
        inp_img = Variable(inp_img).type(Tensor).unsqueeze(0)
        # generate enhanced image
        s = time.time()
        gen_img = model(inp_img)
        times.append(time.time()-s)
        # save output
        img_sample = gen_img.data
        #img_sample = torch.cat((inp_img.data, gen_img.data), -1)
        save_image(img_sample, join(dir_name, basename(path)), normalize=True)
        print ("Tested: %s" % path)

    if (len(times) > 1):
        print ("\nTotal samples: %d" % len(test_files)) 
        # accumulate frame processing times (without bootstrap)
        Ttime, Mtime = np.sum(times[1:]), np.mean(times[1:]) 
        print ("Time taken: %d sec at %0.3f fps" %(Ttime, 1./Mtime))
        print("Saved generated images in in %s\n" %(opt.sample_dir))

checkpoints/FunieGAN(NLSCA_AdaB_L_RA)/EUVP/generator_1.pth
checkpoints/FunieGAN(NLSCA_AdaB_L_RA)/EUVP/generator_1.pth
Loaded model from checkpoints/FunieGAN(NLSCA_AdaB_L_RA)/EUVP/generator_1.pth
Tested: EUVP/test_samples/Inp\test_p0_.jpg
Tested: EUVP/test_samples/Inp\test_p100_.jpg
Tested: EUVP/test_samples/Inp\test_p101_.jpg
Tested: EUVP/test_samples/Inp\test_p102_.jpg
Tested: EUVP/test_samples/Inp\test_p104_.jpg
Tested: EUVP/test_samples/Inp\test_p105_.jpg
Tested: EUVP/test_samples/Inp\test_p106_.jpg
Tested: EUVP/test_samples/Inp\test_p107_.jpg
Tested: EUVP/test_samples/Inp\test_p109_.jpg
Tested: EUVP/test_samples/Inp\test_p110_.jpg
Tested: EUVP/test_samples/Inp\test_p112_.jpg
Tested: EUVP/test_samples/Inp\test_p113_.jpg
Tested: EUVP/test_samples/Inp\test_p114_.jpg
Tested: EUVP/test_samples/Inp\test_p115_.jpg
Tested: EUVP/test_samples/Inp\test_p116_.jpg
Tested: EUVP/test_samples/Inp\test_p117_.jpg
Tested: EUVP/test_samples/Inp\test_p118_.jpg
Tested: EUVP/test_samples/Inp\test_p119_.j

In [14]:

for i in range(0,11):

    generator = f"checkpoints/FunieGAN(noattention)/EUVP/generator_{i}.pth"
    print(generator) 
    parser = argparse.ArgumentParser()
    parser.add_argument("--data_dir", type=str, default=r"EUVP/Paired/underwater_imagenet/trainA")
    parser.add_argument("--sample_dir", type=str, default=r"EUVP/test_samples/result/metricsevaluation/noattention/underwater_imagenet")
    parser.add_argument("--model_name", type=str, default="funiegan") # or "ugan"
    parser.add_argument("--model_path", type=str, default=generator)
    opt,unknown = parser.parse_known_args()

    print(opt.model_path)

    assert exists(opt.model_path), "model not found"
    os.makedirs(opt.sample_dir, exist_ok=True)
    is_cuda = torch.cuda.is_available()
    Tensor = torch.cuda.FloatTensor if is_cuda else torch.FloatTensor 

    if opt.model_name.lower()=='funiegan':
        from PyTorch.nets import funiegan
        model = funiegan.GeneratorFunieGAN()
    elif opt.model_name.lower()=='ugan':
        from nets.ugan import UGAN_Nets
        model = UGAN_Nets(base_model='pix2pix').netG
    else: 
        # other models
        pass

    model.load_state_dict(torch.load(opt.model_path))
    if is_cuda: model.cuda()
    model.eval()
    print ("Loaded model from %s" % (opt.model_path))

    ## data pipeline
    img_width, img_height, channels = 256, 256, 3
    transforms_ = [transforms.Resize((img_height, img_width), Image.BICUBIC),
                transforms.ToTensor(),
                transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),]
    transform = transforms.Compose(transforms_)

    dir_name = join(opt.sample_dir, f"generator_{i}")
    os.makedirs(dir_name, exist_ok=True)

    times = []
    test_files = sorted(glob(join(opt.data_dir, "*.*")))
    for path in test_files:
        inp_img = transform(Image.open(path))
        inp_img = Variable(inp_img).type(Tensor).unsqueeze(0)
        # generate enhanced image
        s = time.time()
        gen_img = model(inp_img)
        times.append(time.time()-s)
        # save output
        img_sample = gen_img.data
        #img_sample = torch.cat((inp_img.data, gen_img.data), -1)
        save_image(img_sample, join(dir_name, basename(path)), normalize=True)
        print ("Tested: %s" % path)

    if (len(times) > 1):
        print ("\nTotal samples: %d" % len(test_files)) 
        # accumulate frame processing times (without bootstrap)
        Ttime, Mtime = np.sum(times[1:]), np.mean(times[1:]) 
        print ("Time taken: %d sec at %0.3f fps" %(Ttime, 1./Mtime))
        print("Saved generated images in in %s\n" %(opt.sample_dir))

checkpoints/FunieGAN(noattention)/EUVP/generator_0.pth
checkpoints/FunieGAN(noattention)/EUVP/generator_0.pth
Loaded model from checkpoints/FunieGAN(noattention)/EUVP/generator_0.pth
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_1010.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10100.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10137.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10207.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10269.jpg


C:\Users\alapa\AppData\Local\Temp\ipykernel_2756\2397588869.py:29: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load(opt.model_path))


Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10373.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10374.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_1054.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10605.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10606.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10607.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10754.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10768.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_10903.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_11015.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_11078.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_1119.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_1124.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_11391.jpg
Tested: EUVP/Paired/underwater_imagenet/trainA\n01496331_11438.jp

In [15]:

for i in range(0,11):

    generator = f"checkpoints/FunieGAN(noattention)/EUVP/generator_{i}.pth"
    print(generator) 
    parser = argparse.ArgumentParser()
    parser.add_argument("--data_dir", type=str, default=r"EUVP/Paired/underwater_scenes/trainA")
    parser.add_argument("--sample_dir", type=str, default=r"EUVP/test_samples/result/metricsevaluation/noattention/underwater_scenes")
    parser.add_argument("--model_name", type=str, default="funiegan") # or "ugan"
    parser.add_argument("--model_path", type=str, default=generator)
    opt,unknown = parser.parse_known_args()

    print(opt.model_path)

    assert exists(opt.model_path), "model not found"
    os.makedirs(opt.sample_dir, exist_ok=True)
    is_cuda = torch.cuda.is_available()
    Tensor = torch.cuda.FloatTensor if is_cuda else torch.FloatTensor 

    if opt.model_name.lower()=='funiegan':
        from PyTorch.nets import funiegan
        model = funiegan.GeneratorFunieGAN()
    elif opt.model_name.lower()=='ugan':
        from nets.ugan import UGAN_Nets
        model = UGAN_Nets(base_model='pix2pix').netG
    else: 
        # other models
        pass

    model.load_state_dict(torch.load(opt.model_path))
    if is_cuda: model.cuda()
    model.eval()
    print ("Loaded model from %s" % (opt.model_path))

    ## data pipeline
    img_width, img_height, channels = 256, 256, 3
    transforms_ = [transforms.Resize((img_height, img_width), Image.BICUBIC),
                transforms.ToTensor(),
                transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),]
    transform = transforms.Compose(transforms_)

    dir_name = join(opt.sample_dir, f"generator_{i}")
    os.makedirs(dir_name, exist_ok=True)

    times = []
    test_files = sorted(glob(join(opt.data_dir, "*.*")))
    for path in test_files:
        inp_img = transform(Image.open(path))
        inp_img = Variable(inp_img).type(Tensor).unsqueeze(0)
        # generate enhanced image
        s = time.time()
        gen_img = model(inp_img)
        times.append(time.time()-s)
        # save output
        img_sample = gen_img.data
        #img_sample = torch.cat((inp_img.data, gen_img.data), -1)
        save_image(img_sample, join(dir_name, basename(path)), normalize=True)
        print ("Tested: %s" % path)

    if (len(times) > 1):
        print ("\nTotal samples: %d" % len(test_files)) 
        # accumulate frame processing times (without bootstrap)
        Ttime, Mtime = np.sum(times[1:]), np.mean(times[1:]) 
        print ("Time taken: %d sec at %0.3f fps" %(Ttime, 1./Mtime))
        print("Saved generated images in in %s\n" %(opt.sample_dir))

checkpoints/FunieGAN(noattention)/EUVP/generator_0.pth
checkpoints/FunieGAN(noattention)/EUVP/generator_0.pth
Loaded model from checkpoints/FunieGAN(noattention)/EUVP/generator_0.pth
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1000_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1001_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1002_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1003_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1004_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1005_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1007_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1009_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f100_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1011_.jpg


C:\Users\alapa\AppData\Local\Temp\ipykernel_2756\3807194912.py:29: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  model.load_state_dict(torch.load(opt.model_path))


Tested: EUVP/Paired/underwater_scenes/trainA\im_f1012_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1013_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1015_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1018_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f101_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1022_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1026_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1027_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1029_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1033_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1034_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1035_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1036_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1037_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1038_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f103_.jpg
Tested: EUVP/Paired/underwater_scenes/trainA\im_f1041_.jpg

In [ ]:
### unwanted section

import argparse

#for i in range(0,20):

generator = f"checkpoints/FunieGAN(A1)/EUVP/generator_0.pth"
print(generator) 
parser = argparse.ArgumentParser()
parser.add_argument("--data_dir", type=str, default=r"EUVP/test_samples/Inp")
parser.add_argument("--sample_dir", type=str, default=r"EUVP/test_samples/result/batch1")
parser.add_argument("--model_name", type=str, default="funiegan") # or "ugan"
parser.add_argument("--model_path", type=str, default=generator)
opt,unknown = parser.parse_known_args()

print(opt.model_path)

assert exists(opt.model_path), "model not found"
os.makedirs(opt.sample_dir, exist_ok=True)
is_cuda = torch.cuda.is_available()
Tensor = torch.cuda.FloatTensor if is_cuda else torch.FloatTensor 

if opt.model_name.lower()=='funiegan':
    from PyTorch.nets import funiegan
    model = funiegan.GeneratorFunieGAN()
elif opt.model_name.lower()=='ugan':
    from nets.ugan import UGAN_Nets
    model = UGAN_Nets(base_model='pix2pix').netG
else: 
    # other models
    pass

model.load_state_dict(torch.load(opt.model_path))
if is_cuda: model.cuda()
model.eval()
print ("Loaded model from %s" % (opt.model_path))

## data pipeline
img_width, img_height, channels = 256, 256, 3
transforms_ = [transforms.Resize((img_height, img_width), Image.BICUBIC),
            transforms.ToTensor(),
            transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),]
transform = transforms.Compose(transforms_)

dir_name = join(opt.sample_dir, f"generator_0")
os.makedirs(dir_name, exist_ok=True)

times = []
test_files = sorted(glob(join(opt.data_dir, "*.*")))
for path in test_files:
    inp_img = transform(Image.open(path))
    inp_img = Variable(inp_img).type(Tensor).unsqueeze(0)
    # generate enhanced image
    s = time.time()
    gen_img = model(inp_img)
    times.append(time.time()-s)
    # save output
    img_sample = torch.cat((inp_img.data, gen_img.data), -1)
    save_image(img_sample, join(dir_name, basename(path)), normalize=True)
    print ("Tested: %s" % path)

if (len(times) > 1):
    print ("\nTotal samples: %d" % len(test_files)) 
    # accumulate frame processing times (without bootstrap)
    Ttime, Mtime = np.sum(times[1:]), np.mean(times[1:]) 
    print ("Time taken: %d sec at %0.3f fps" %(Ttime, 1./Mtime))
    print("Saved generated images in in %s\n" %(opt.sample_dir))

In [ ]:
### single model test

import argparse

#for i in range(0,20):
i = 4
generator = f"checkpoints/FunieGAN(A3)/EUVP/generator_{i}.pth"
print(generator) 
parser = argparse.ArgumentParser()
parser.add_argument("--data_dir", type=str, default=r"EUVP/Paired/underwater_dark/trainA")
parser.add_argument("--sample_dir", type=str, default=r"EUVP/test_samples/result/metricsevaluation/underwater_dark")
parser.add_argument("--model_name", type=str, default="funiegan") # or "ugan"
parser.add_argument("--model_path", type=str, default=generator)
opt,unknown = parser.parse_known_args()

print(opt.model_path)

assert exists(opt.model_path), "model not found"
os.makedirs(opt.sample_dir, exist_ok=True)
is_cuda = torch.cuda.is_available()
Tensor = torch.cuda.FloatTensor if is_cuda else torch.FloatTensor 

if opt.model_name.lower()=='funiegan':
    from PyTorch.nets import A2funiegan
    model = A2funiegan.GeneratorFunieGAN()
elif opt.model_name.lower()=='ugan':
    from nets.ugan import UGAN_Nets
    model = UGAN_Nets(base_model='pix2pix').netG
else: 
    # other models
    pass

model.load_state_dict(torch.load(opt.model_path))
if is_cuda: model.cuda()
model.eval()
print ("Loaded model from %s" % (opt.model_path))

## data pipeline
img_width, img_height, channels = 256, 256, 3
transforms_ = [transforms.Resize((img_height, img_width), Image.BICUBIC),
            transforms.ToTensor(),
            transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5)),]
transform = transforms.Compose(transforms_)

dir_name = join(opt.sample_dir, f"generator_{i}")
os.makedirs(dir_name, exist_ok=True)

times = []
test_files = sorted(glob(join(opt.data_dir, "*.*")))
for path in test_files:
    inp_img = transform(Image.open(path))
    inp_img = Variable(inp_img).type(Tensor).unsqueeze(0)
    # generate enhanced image
    s = time.time()
    gen_img = model(inp_img)
    times.append(time.time()-s)
    # save output
    img_sample = torch.cat((inp_img.data, gen_img.data), -1)
    save_image(img_sample, join(dir_name, basename(path)), normalize=True)
    print ("Tested: %s" % path)

if (len(times) > 1):
    print ("\nTotal samples: %d" % len(test_files)) 
    # accumulate frame processing times (without bootstrap)
    Ttime, Mtime = np.sum(times[1:]), np.mean(times[1:]) 
    print ("Time taken: %d sec at %0.3f fps" %(Ttime, 1./Mtime))
    print("Saved generated images in in %s\n" %(opt.sample_dir))